# Pose Error Project
### (Transformer-Encoder)

In [1]:
import logging

logging.basicConfig(format='%(asctime)s | %(levelname)s : %(message)s', level=logging.INFO)
logger = logging.getLogger(__name__)

logger.info("Loading packages ...")
import os
import sys
import time
import pickle
import json

# 3rd party packages

#from tqdm import tqdm
# since we are using it in jupyter notebook
from tqdm.notebook import tqdm

import torch
from torch.utils.data import DataLoader
from torch.utils.tensorboard import SummaryWriter

# Project modules
from options import Options
from running import setup, pipeline_factory, validate, check_progress, NEG_METRICS
from utils import utils
from datasets.data import data_factory, Normalizer
from datasets.datasplit import split_dataset
from models.ts_transformer import model_factory
from models.loss import get_loss_module
from optimizers import get_optimizer

import parser


2023-05-26 00:14:02,711 | INFO : Loading packages ...
2023-05-26 00:14:04,385 | INFO : Note: NumExpr detected 32 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
2023-05-26 00:14:04,386 | INFO : NumExpr defaulting to 8 threads.


# Setup Configurations

In [2]:
# Finetune
pretrain_folder = "poseErrorPred_preTrain_2023-05-25_21-30-51_HallLiving"

model_path = "../experiments/{}/checkpoints/model_best.pth".format(pretrain_folder)

#normal_path = "../experiments/{}/normalization.pickle".format(pretrain_folder)

text = "--output_dir ../experiments --comment 'poseErrorPred_finetune_from_HallLiving' \
        --name poseErrorPred_finetuned --records_file Regression_records.xls \
        --data_dir ../data/SenseTimeV4_Selective/ --data_class pose \
        --epochs 25 --lr 0.0001 --optimizer RAdam \
        --pos_encoding learnable\
        --load_model {} \
        --task regression --change_output --batch_size 128\
        --num_layers 3  --num_heads 8 --d_model 64 --dim_feedforward 256 \
        --gpu 2  --val_interval 1".format(model_path)


In [3]:
# Process the setting string
# Generate the config variable
input_text = text.split()
args = Options().parse(input_text)
config = setup(args)

2023-05-26 00:14:05,751 | INFO : Stored configuration file in '../experiments/poseErrorPred_finetuned_2023-05-26_00-14-05_6pl'


In [4]:
config

{'config_filepath': None,
 'output_dir': '../experiments/poseErrorPred_finetuned_2023-05-26_00-14-05_6pl',
 'data_dir': '../data/SenseTimeV4_Selective/',
 'load_model': '../experiments/poseErrorPred_preTrain_2023-05-25_21-30-51_HallLiving/checkpoints/model_best.pth',
 'resume': False,
 'change_output': True,
 'save_all': False,
 'experiment_name': 'poseErrorPred_finetuned',
 'comment': "'poseErrorPred_finetune_from_HallLiving'",
 'no_timestamp': False,
 'records_file': 'Regression_records.xls',
 'console': False,
 'print_interval': 1,
 'gpu': '2',
 'n_proc': -1,
 'num_workers': 0,
 'seed': None,
 'limit_size': None,
 'test_only': None,
 'data_class': 'pose',
 'labels': None,
 'test_from': None,
 'test_ratio': 0,
 'val_ratio': 0.2,
 'pattern': None,
 'val_pattern': None,
 'test_pattern': None,
 'normalization': 'standardization',
 'norm_from': None,
 'subsample_factor': None,
 'task': 'regression',
 'masking_ratio': 0.15,
 'mean_mask_length': 3,
 'mask_mode': 'separate',
 'mask_distribu

# Setup Logger

In [5]:
total_epoch_time = 0
total_eval_time = 0

total_start_time = time.time()

In [6]:
# Add file logging besides stdout
file_handler = logging.FileHandler(os.path.join(config['output_dir'], 'output.log'))
logger.addHandler(file_handler)

logger.info('Running:\n{}\n'.format(' '.join(sys.argv)))  # command used to run

2023-05-26 00:14:08,144 | INFO : Running:
/home/tianyi/anaconda3/envs/transformer/lib/python3.8/site-packages/ipykernel_launcher.py -f /home/tianyi/.local/share/jupyter/runtime/kernel-93009e48-e2f4-4eaf-aab0-66d5e254c727.json



# Setup Training Device

In [7]:
if config['seed'] is not None:
    torch.manual_seed(config['seed'])

device = torch.device('cuda:2' if (torch.cuda.is_available() and config['gpu'] != '-1') else 'cpu')
logger.info("Using device: {}".format(device))
if device == 'cuda:2':
    logger.info("Device index: {}".format(torch.cuda.current_device()))

2023-05-26 00:14:09,449 | INFO : Using device: cuda:2


# Prepare Data

In [8]:
 # Build data
logger.info("Loading and preprocessing data ...")
data_class = data_factory[config['data_class']]
my_data = data_class(config['data_dir'], 
                     pattern=config['pattern'], 
                     n_proc=config['n_proc'], 
                     limit_size=config['limit_size'], 
                     config=config)
feat_dim = my_data.feature_df.shape[1]  # dimensionality of data features
if config['task'] == 'classification':
    validation_method = 'StratifiedShuffleSplit'
    labels = my_data.labels_df.values.flatten()
else:
    validation_method = 'ShuffleSplit'
    labels = None
    
# Modify for the pose error pred
validation_method = 'PoseErrorTimeSplit'
validation_method = 'PoseErrorSequenceSplit'

2023-05-26 00:14:10,382 | INFO : Loading and preprocessing data ...
2023-05-26 00:14:10,384 | INFO : Loading 69 datasets files using 32 parallel processes ...


# Split dataset

In [9]:
# Split dataset
test_data = my_data
test_indices = None  # will be converted to empty list in `split_dataset`, if also test_set_ratio == 0
val_data = my_data
val_indices = []
if config['test_pattern']:  # used if test data come from different files / file patterns
    test_data = data_class(config['data_dir'], pattern=config['test_pattern'], n_proc=-1, config=config)
    test_indices = test_data.all_IDs
if config['test_from']:  # load test IDs directly from file, if available, otherwise use `test_set_ratio`. Can work together with `test_pattern`
    test_indices = list(set([line.rstrip() for line in open(config['test_from']).readlines()]))
    try:
        test_indices = [int(ind) for ind in test_indices]  # integer indices
    except ValueError:
        pass  # in case indices are non-integers
    logger.info("Loaded {} test IDs from file: '{}'".format(len(test_indices), config['test_from']))
if config['val_pattern']:  # used if val data come from different files / file patterns
    val_data = data_class(config['data_dir'], pattern=config['val_pattern'], n_proc=-1, config=config)
    val_indices = val_data.all_IDs

In [10]:
# Note: currently a validation set must exist, either with `val_pattern` or `val_ratio`
# Using a `val_pattern` means that `val_ratio` == 0 and `test_ratio` == 0
if config['val_ratio'] > 0:
    train_indices, val_indices, test_indices = split_dataset(data_indices=my_data.all_IDs,
                                                             validation_method=validation_method,
                                                             n_splits=1,
                                                             validation_ratio=config['val_ratio'],
                                                             test_set_ratio=config['test_ratio'],  # used only if test_indices not explicitly specified
                                                             test_indices=test_indices,
                                                             random_seed=1337,
                                                             labels=labels)
    train_indices = train_indices[0]  # `split_dataset` returns a list of indices *per fold/split*
    val_indices = val_indices[0]  # `split_dataset` returns a list of indices *per fold/split*
else:
    train_indices = my_data.all_IDs
    if test_indices is None:
        test_indices = []

In [11]:
train_cv_indices, val_cv_indices, test_indices = split_dataset(data_indices=my_data.all_IDs,
                                                         validation_method=validation_method,
                                                         n_splits=1,
                                                         validation_ratio=config['val_ratio'],
                                                         test_set_ratio=config['test_ratio'],  # used only if test_indices not explicitly specified
                                                         test_indices=test_indices,
                                                         random_seed=1337,
                                                         labels=labels)
train_cv_indices

[[110100200000,
  110100200001,
  110100200002,
  110100200003,
  110100200004,
  110100200005,
  110100200006,
  110100200007,
  110100200008,
  110100200009,
  110100200010,
  110100200011,
  110100200012,
  110100200013,
  110100200014,
  110100200015,
  110100200016,
  110100200017,
  110100200018,
  110100200019,
  110100200020,
  110100200021,
  110100200022,
  110100200023,
  110100200024,
  110100200025,
  110100200026,
  110100200027,
  110100200028,
  110100200029,
  110100200030,
  110100200031,
  110100200032,
  110100200033,
  110100200034,
  110100200035,
  110100200036,
  110100200037,
  110100200038,
  110100200039,
  110100200040,
  110100200041,
  110100200042,
  110100200043,
  110100200044,
  110100200045,
  110100200046,
  110100200047,
  110100200048,
  110100200049,
  110100200050,
  110100200051,
  110100200052,
  110100200053,
  110100200054,
  110100200055,
  110100200056,
  110100200057,
  110100200058,
  110100200059,
  110100200060,
  110100200061,
  110100

In [12]:
len(train_cv_indices)

8

In [13]:
train_cv_indices[1][-1]

110701001717

In [14]:
len(val_cv_indices[0])

11546

In [15]:
logger.info("{} \t samples may be used for training".format(len(train_cv_indices[0])))
logger.info("{} \t samples will be used for validation".format(len(val_cv_indices[0])))
logger.info("{} \t samples will be used for testing".format(len(test_indices)))

2023-05-26 00:14:44,932 | INFO : 98106 	 samples may be used for training
2023-05-26 00:14:44,933 | INFO : 11546 	 samples will be used for validation
2023-05-26 00:14:44,933 | INFO : 0 	 samples will be used for testing


In [16]:
for cv_idx in range(len(train_cv_indices)):
    print(cv_idx)
    train_indices = train_cv_indices[cv_idx]
    val_indices = val_cv_indices[cv_idx]
    with open(os.path.join(config['output_dir'], 'data_indices.json'), 'w') as f:
        try:
            json.dump({'train_indices': list(map(int, train_indices)),
                       'val_indices': list(map(int, val_indices)),
                       'test_indices': list(map(int, test_indices))}, f, indent=4)
        except ValueError:  # in case indices are non-integers
            json.dump({'train_indices': list(train_indices),
                       'val_indices': list(val_indices),
                       'test_indices': list(test_indices)}, f, indent=4)
    
    ## Pre-process features
    normalizer = None
    if config['norm_from']:
        with open(config['norm_from'], 'rb') as f:
            norm_dict = pickle.load(f)
        normalizer = Normalizer(**norm_dict)
    elif config['normalization'] is not None:
        normalizer = Normalizer(config['normalization'])
        my_data.feature_df.loc[train_indices] = normalizer.normalize(my_data.feature_df.loc[train_indices])
        if not config['normalization'].startswith('per_sample'):
            # get normalizing values from training set and store for future use
            norm_dict = normalizer.__dict__
            with open(os.path.join(config['output_dir'], 'normalization.pickle'), 'wb') as f:
                pickle.dump(norm_dict, f, pickle.HIGHEST_PROTOCOL)
    if normalizer is not None:
        if len(val_indices):
            val_data.feature_df.loc[val_indices] = normalizer.normalize(val_data.feature_df.loc[val_indices])
        if len(test_indices):
            test_data.feature_df.loc[test_indices] = normalizer.normalize(test_data.feature_df.loc[test_indices])
            
    ## Create model
    logger.info("Creating model ...")
    model = model_factory(config, my_data)

    if config['freeze']:
        for name, param in model.named_parameters():
            if name.startswith('output_layer'):
                param.requires_grad = True
            else:
                param.requires_grad = False

    logger.info("Model:\n{}".format(model))
    logger.info("Total number of parameters: {}".format(utils.count_parameters(model)))
    logger.info("Trainable parameters: {}".format(utils.count_parameters(model, trainable=True)))
    
    
    ## Initialize optimizer
    if config['global_reg']:
        weight_decay = config['l2_reg']
        output_reg = None
    else:
        weight_decay = 0
        output_reg = config['l2_reg']

    optim_class = get_optimizer(config['optimizer'])
    optimizer = optim_class(model.parameters(), lr=config['lr'], weight_decay=weight_decay)

    start_epoch = 0
    lr_step = 0  # current step index of `lr_step`
    lr = config['lr']  # current learning step
    # Load model and optimizer state
    if args.load_model:
        model, optimizer, start_epoch = utils.load_model(model, config['load_model'], optimizer, config['resume'],
                                                         config['change_output'],
                                                         config['lr'],
                                                         config['lr_step'],
                                                         config['lr_factor'])
    model.to(device)

    loss_module = get_loss_module(config)
    
    
    if config['test_only'] == 'testset':  # Only evaluate and skip training
        dataset_class, collate_fn, runner_class = pipeline_factory(config)
        test_dataset = dataset_class(test_data, test_indices)

        test_loader = DataLoader(dataset=test_dataset,
                                 batch_size=config['batch_size'],
                                 shuffle=False,
                                 num_workers=config['num_workers'],
                                 pin_memory=True,
                                 collate_fn=lambda x: collate_fn(x, max_len=model.max_len))
        test_evaluator = runner_class(model, test_loader, device, loss_module,
                                            print_interval=config['print_interval'], console=config['console'])
        aggr_metrics_test, per_batch_test = test_evaluator.evaluate(keep_all=True)
        print_str = 'Test Summary: '
        for k, v in aggr_metrics_test.items():
            print_str += '{}: {:8f} | '.format(k, v)
        logger.info(print_str)
        #return
        
    # Initialize data generators
    if config['test_only'] != 'testset':  # Only evaluate and skip training
        dataset_class, collate_fn, runner_class = pipeline_factory(config)
        val_dataset = dataset_class(val_data, val_indices)

        val_loader = DataLoader(dataset=val_dataset,
                                batch_size=config['batch_size'],
                                shuffle=False,
                                num_workers=config['num_workers'],
                                pin_memory=True,
                                collate_fn=lambda x: collate_fn(x, max_len=model.max_len))

        train_dataset = dataset_class(my_data, train_indices)

        train_loader = DataLoader(dataset=train_dataset,
                                  batch_size=config['batch_size'],
                                  shuffle=True,
                                  num_workers=config['num_workers'],
                                  pin_memory=True,
                                  collate_fn=lambda x: collate_fn(x, max_len=model.max_len))

        trainer = runner_class(model, train_loader, device, loss_module, optimizer, l2_reg=output_reg,
                                     print_interval=config['print_interval'], console=config['console'])
        val_evaluator = runner_class(model, val_loader, device, loss_module,
                                           print_interval=config['print_interval'], console=config['console'])

        tensorboard_writer = SummaryWriter(config['tensorboard_dir'])

        best_value = 1e16 if config['key_metric'] in NEG_METRICS else -1e16  # initialize with +inf or -inf depending on key metric
        metrics = []  # (for validation) list of lists: for each epoch, stores metrics like loss, ...
        best_metrics = {}
        
        
    ## Evaluate before training
    aggr_metrics_val, best_metrics, best_value = validate(val_evaluator, tensorboard_writer, config, best_metrics,
                                                      best_value, epoch=0)
    metrics_names, metrics_values = zip(*aggr_metrics_val.items())
    metrics.append(list(metrics_values))
    
    
    ## Start training
    logger.info('Starting training...')
    for epoch in tqdm(range(start_epoch + 1, config["epochs"] + 1), desc='Training Epoch', leave=False):
        mark = epoch if config['save_all'] else 'last'
        epoch_start_time = time.time()
        # Training
        aggr_metrics_train = trainer.train_epoch(epoch)  # dictionary of aggregate epoch metrics
        epoch_runtime = time.time() - epoch_start_time
        print()
        print_str = 'Epoch {} Training Summary: '.format(epoch)
        for k, v in aggr_metrics_train.items():
            tensorboard_writer.add_scalar('{}/train'.format(k), v, epoch)
            print_str += '{}: {:8f} | '.format(k, v)
        logger.info(print_str)
        logger.info("Epoch runtime: {} hours, {} minutes, {} seconds\n".format(*utils.readable_time(epoch_runtime)))
        total_epoch_time += epoch_runtime
        avg_epoch_time = total_epoch_time / (epoch - start_epoch)
        avg_batch_time = avg_epoch_time / len(train_loader)
        avg_sample_time = avg_epoch_time / len(train_dataset)
        logger.info("Avg epoch train. time: {} hours, {} minutes, {} seconds".format(*utils.readable_time(avg_epoch_time)))
        logger.info("Avg batch train. time: {} seconds".format(avg_batch_time))
        logger.info("Avg sample train. time: {} seconds".format(avg_sample_time))

        # evaluate if first or last epoch or at specified interval
        if (epoch == config["epochs"]) or (epoch == start_epoch + 1) or (epoch % config['val_interval'] == 0):
            aggr_metrics_val, best_metrics, best_value = validate(val_evaluator, tensorboard_writer, config,
                                                                  best_metrics, best_value, epoch)
            metrics_names, metrics_values = zip(*aggr_metrics_val.items())
            metrics.append(list(metrics_values))

        utils.save_model(os.path.join(config['save_dir'], 'model_{}.pth'.format(mark)), epoch, model, optimizer)

        # Learning rate scheduling
        if epoch == config['lr_step'][lr_step]:
            utils.save_model(os.path.join(config['save_dir'], 'model_{}.pth'.format(epoch)), epoch, model, optimizer)
            lr = lr * config['lr_factor'][lr_step]
            if lr_step < len(config['lr_step']) - 1:  # so that this index does not get out of bounds
                lr_step += 1
            logger.info('Learning rate updated to: ', lr)
            for param_group in optimizer.param_groups:
                param_group['lr'] = lr

        # Difficulty scheduling
        if config['harden'] and check_progress(epoch):
            train_loader.dataset.update()
            val_loader.dataset.update()
            
    # Export evolution of metrics over epochs
    header = metrics_names
    metrics_filepath = os.path.join(config["output_dir"], "metrics_" + config["experiment_name"] + ".xls")
    book = utils.export_performance_metrics(metrics_filepath, metrics, header, sheet_name="metrics")

    # Export record metrics to a file accumulating records from all experiments
    utils.register_record(config["records_file"], config["initial_timestamp"], config["experiment_name"],
                          best_metrics, aggr_metrics_val, comment=config['comment'])

    logger.info('Best {} was {}. Other metrics: {}'.format(config['key_metric'], best_value, best_metrics))
    logger.info('All Done!')

    total_runtime = time.time() - total_start_time
    logger.info("Total runtime: {} hours, {} minutes, {} seconds\n".format(*utils.readable_time(total_runtime)))

    #return best_value
    print(best_value)
    
    source_path = config['pred_dir'] + '/best_predictions.npz'
    target_path = config['pred_dir'] + "/best_predictions_{}.npz".format(cv_idx)
    os.rename(source_path, target_path)


0


2023-05-26 00:14:55,778 | INFO : Creating model ...
2023-05-26 00:14:55,816 | INFO : Model:
TSTransformerEncoderClassiregressor(
  (project_inp): Linear(in_features=13, out_features=64, bias=True)
  (pos_enc): LearnablePositionalEncoding(
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (transformer_encoder): TransformerEncoder(
    (layers): ModuleList(
      (0): TransformerBatchNormEncoderLayer(
        (self_attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=64, out_features=64, bias=True)
        )
        (linear1): Linear(in_features=64, out_features=256, bias=True)
        (dropout): Dropout(p=0.1, inplace=False)
        (linear2): Linear(in_features=256, out_features=64, bias=True)
        (norm1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (norm2): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (dropout1): Dropout(p=0.1, inplace=False)
        (dro

Loaded model from ../experiments/poseErrorPred_preTrain_2023-05-25_21-30-51_HallLiving/checkpoints/model_best.pth. Epoch: 27


2023-05-26 00:15:03,865 | INFO : Evaluating on validation set ...


Evaluating Epoch 0   0.0% | batch:         0 of        91	|	loss: 28.3447
Evaluating Epoch 0   1.1% | batch:         1 of        91	|	loss: 20.5903
Evaluating Epoch 0   2.2% | batch:         2 of        91	|	loss: 1.33969
Evaluating Epoch 0   3.3% | batch:         3 of        91	|	loss: 22.3136
Evaluating Epoch 0   4.4% | batch:         4 of        91	|	loss: 4.04378
Evaluating Epoch 0   5.5% | batch:         5 of        91	|	loss: 41.758
Evaluating Epoch 0   6.6% | batch:         6 of        91	|	loss: 73.3874
Evaluating Epoch 0   7.7% | batch:         7 of        91	|	loss: 26.5145
Evaluating Epoch 0   8.8% | batch:         8 of        91	|	loss: 26.0106
Evaluating Epoch 0   9.9% | batch:         9 of        91	|	loss: 1.58529
Evaluating Epoch 0  11.0% | batch:        10 of        91	|	loss: 15.6261
Evaluating Epoch 0  12.1% | batch:        11 of        91	|	loss: 3.81705
Evaluating Epoch 0  13.2% | batch:        12 of        91	|	loss: 32.124
Evaluating Epoch 0  14.3% | batch:      

...

2023-05-26 00:54:47,658 | INFO : Validation runtime: 0.0 hours, 0.0 minutes, 1.2826464176177979 seconds



Evaluating Epoch 6  85.4% | batch:        41 of        48	|	loss: 0.911804
Evaluating Epoch 6  87.5% | batch:        42 of        48	|	loss: 0.46588
Evaluating Epoch 6  89.6% | batch:        43 of        48	|	loss: 0.944865
Evaluating Epoch 6  91.7% | batch:        44 of        48	|	loss: 13.2527
Evaluating Epoch 6  93.8% | batch:        45 of        48	|	loss: 6.42937
Evaluating Epoch 6  95.8% | batch:        46 of        48	|	loss: 16.6135
Evaluating Epoch 6  97.9% | batch:        47 of        48	|	loss: 9.94361


2023-05-26 00:54:47,662 | INFO : Avg val. time: 0.0 hours, 0.0 minutes, 2.6941793890560373 seconds
2023-05-26 00:54:47,663 | INFO : Avg batch val. time: 0.056128737272000774 seconds
2023-05-26 00:54:47,663 | INFO : Avg sample val. time: 0.0004386485491787752 seconds
2023-05-26 00:54:47,664 | INFO : Epoch 6 Validation Summary: epoch: 6.000000 | loss: 6.252289 | 



Training Epoch 7   0.0% | batch:         0 of       809	|	loss: 0.43062
Training Epoch 7   0.1% | batch:         1 of       809	|	loss: 0.407987
Training Epoch 7   0.2% | batch:         2 of       809	|	loss: 0.534187
Training Epoch 7   0.4% | batch:         3 of       809	|	loss: 0.419247
Training Epoch 7   0.5% | batch:         4 of       809	|	loss: 0.428675
Training Epoch 7   0.6% | batch:         5 of       809	|	loss: 0.378901
Training Epoch 7   0.7% | batch:         6 of       809	|	loss: 0.327674
Training Epoch 7   0.9% | batch:         7 of       809	|	loss: 0.693598
Training Epoch 7   1.0% | batch:         8 of       809	|	loss: 0.333017
Training Epoch 7   1.1% | batch:         9 of       809	|	loss: 0.309056
Training Epoch 7   1.2% | batch:        10 of       809	|	loss: 0.586926
Training Epoch 7   1.4% | batch:        11 of       809	|	loss: 0.427884
Training Epoch 7   1.5% | batch:        12 of       809	|	loss: 0.563386
Training Epoch 7   1.6% | batch:        13 of      

Training Epoch 7  14.5% | batch:       117 of       809	|	loss: 0.37641
Training Epoch 7  14.6% | batch:       118 of       809	|	loss: 0.39952
Training Epoch 7  14.7% | batch:       119 of       809	|	loss: 0.594699
Training Epoch 7  14.8% | batch:       120 of       809	|	loss: 0.39799
Training Epoch 7  15.0% | batch:       121 of       809	|	loss: 0.585888
Training Epoch 7  15.1% | batch:       122 of       809	|	loss: 0.553227
Training Epoch 7  15.2% | batch:       123 of       809	|	loss: 0.684463
Training Epoch 7  15.3% | batch:       124 of       809	|	loss: 1.58346
Training Epoch 7  15.5% | batch:       125 of       809	|	loss: 0.4259
Training Epoch 7  15.6% | batch:       126 of       809	|	loss: 0.387217
Training Epoch 7  15.7% | batch:       127 of       809	|	loss: 0.612598
Training Epoch 7  15.8% | batch:       128 of       809	|	loss: 0.435678
Training Epoch 7  15.9% | batch:       129 of       809	|	loss: 0.803632
Training Epoch 7  16.1% | batch:       130 of       809	|

In [17]:
os.rename(source_path, target_path)

In [ ]:
source_path = config['pred_dir'] + '/best_predictions.npz'
target_path = config['pred_dir'] + "/best_predictions_{}.npz".format(cv_idx)

# Evaluation

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

In [ ]:
idx = 0

In [ ]:
total_path = config['pred_dir'] + "/best_predictions_{}.npz".format(idx)
total_path

In [ ]:
config['pred_dir']

In [ ]:
config['output_dir']

In [ ]:
pred = np.load(total_path, allow_pickle=True)
pred.files

In [ ]:
y = np.concatenate(pred["targets"], axis=0)
y_pred = np.concatenate(pred["predictions"], axis=0)
IDs = np.concatenate(pred["IDs"], axis=0)
y_pred.shape

In [ ]:
def get_mape(y, y_pred):
    err = y - y_pred
    return np.mean(np.abs(err)/y)

def get_mse(y, y_pred):
    err = y - y_pred
    return np.mean(np.square(err))

In [ ]:
get_mse(y, y_pred)

In [ ]:
get_mape(y, y_pred)

In [ ]:
y.shape

In [ ]:
len(val_indices)

In [ ]:
def visualize_output(y, y_pred, title=' '):
    fig, (ax0, ax1) = plt.subplots(2, 1, figsize=(14, 6))
    fig.tight_layout(pad=3.0)
    
    ax0.plot(y, color='g', label='truth')
    ax0.set_title(title)
    ax0.set_xlabel('Step')
    ax0.set_ylabel('Error')
    ax0.grid()
    ax0.legend()
    
    ax1.plot(y, color='g', label='truth')
    ax1.plot(y_pred, color='b', alpha=0.7, label='predict')
    mse = get_mse(y, y_pred)
    mape = get_mape(y, y_pred)
    ax1.set_title(title+"- mse: {:.5f} | mape: {:.5f}".format(mse, mape))
    ax1.set_xlabel('Step')
    ax1.set_ylabel('Error')
    ax1.grid()
    ax1.legend()
    plt.show()

In [ ]:
visualize_output(y, y_pred, title='Prediction on SenseTime Dataset')

In [ ]:
idx += 1